In [0]:
%pip install transformers==4.40.1 langchain==0.1.17 databricks-vectorsearch==0.33 mlflow==2.12.1
dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Obtaining dependency information for transformers==4.40.1 from https://files.pythonhosted.org/packages/cf/90/2596ac2ab49c4df6ff1fceaf7f5afb18401ba2f326348ce1a6261a65e7ed/transformers-4.40.1-py3-none-any.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/138.0 kB ? eta -:--:--
     ━━━━━━━━━━━━━━━━━━━━━━━━━━╸━━━━━━━━━━━━━ 92.2/138.0 kB 2.7 MB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.0/138.0 kB 2.8 MB/s eta 0:00:00
  Obtaining dependency information for langchain==0.1.17 from https://files.pythonhosted.org/packages/c8/bc/607cd3254800a26b60da9e2ca6b10785e60170db7e85dc3d0328b5ab3a9c/langchain-0.1.17-py3-none-any.whl.metadata
  Using cached langchain-0.1.17-py3-none-any.whl.metadata (13 kB)
  Obtaining dependency information for databricks-vectorsearch==0.33 from https://files.pythonhosted.org/packages/93/22/5c0c2eea1e5d7c6789d67ec562bb180841d4e7ef5f349

### Ingesting Markdown files as binary format

In [0]:
volume_folder = '/Volumes/llm_hackathon/default'

df = (spark.readStream
        .format('cloudFiles')
        .option('cloudFiles.format', 'BINARYFILE')
        .option("pathGlobFilter", "*.md")
        .load(f"dbfs:{volume_folder}/edgar/mds"))

# Write the data as a Delta table
(df.writeStream
  .trigger(availableNow=True)
  .option("checkpointLocation", f'dbfs:{volume_folder}/checkpoints/edgar_raw_docs')
  .table('edgar_md').awaitTermination())

In [0]:
%sql
SELECT * FROM edgar_md LIMIT 5

path modificationTime length content dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-028573.md 2024-05-01T14:09:35Z 1115973 CgogCgoKCgrCoArCoAoKCioqVU5JVEVEClNUQVRFUyoqIAoKCioqU0VDVVJJVElFUwpBTkQgRVhDSEFOR0UgQ09NTUlTU0lPTioqCgoKKipXQVNISU5HVE9OLApEQyAyMDU0OSoqIAoKCsKgCgoKKipGT1JNCjEwLUsqKgoKCsI= (truncated) dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001214659-24-006963.md 2024-05-01T14:16:17Z 1108333 CgoKCgoKCgrCoAoKCgrCoAoKKipVTklURUQgU1RBVEVTIFNFQ1VSSVRJRVMgQU5EIEVYQ0hBTkdFIENPTU1JU1NJT04qKgoKCioqV2FzaGluZ3RvbiwgRC5DLiAyMDU0OSoqCgoKCioqRk9STSAxMC1LKioKCgrCoAoKCnggKio= (truncated) dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-032225.md 2024-05-01T14:24:02Z 909727 CgogCgoKCgrCoArCoMKgCgoKKipVTklURUQgU1RBVEVTKioKCgoqKlNFQ1VSSVRJRVMgQU5EIEVYQ0hBTkdFIENPTU1JU1NJT04qKgoKCioqV2FzaGluZ3RvbiwgRC5DLiAyMDU0OSoqCgoKwqAKCgoqKkZPUk0gMTAtSyoqCgo= (truncated) dbfs:/Volumes/llm_hackathon/default/edgar/mds/0000950170-24-038866.md 2024-05-01T14:11:36Z 895801 CgoxMC1LCgoKIyMjIyMgCgogCgoKwqAKCgpVTklURUQgU1RBVEVTCgoKU0VDVVJJVElFUyBBTkQgRVhDSEFOR0UgQ09NTUlTU0lPTgoKCldhc2hpbmd0b24sIEQuQy4gMjA1NDkKCgrCoAoKCkZPUk0gMTAtSwoKCsKgCgoKICg= (truncated) dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001437749-24-010430.md 2024-05-01T14:12:15Z 841350 Cgp6dnJhMjAyMzEyMzFcXzEway5odG0KCgoKIMKgCiAKwqAKCgoKCi0tLQoKCsKgCgoKCgotLS0KCgrCoAoKCioqVU5JVEVEIFNUQVRFUyoqCgoKKipTRUNVUklUSUVTIEFORCBFWENIQU5HRSBDT01NSVNTSU9OKioKCgoqKlc= (truncated)

In [0]:
import io
from pyspark.sql.functions import split, replace, element_at, lit, array_join, explode
from langchain_text_splitters import MarkdownHeaderTextSplitter, RecursiveCharacterTextSplitter
from transformers import AutoTokenizer, OpenAIGPTTokenizer
import pandas as pd
from pyspark.sql.functions import pandas_udf

None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.
Unexpected internal error when monkey patching `PreTrainedModel.from_pretrained`: 
PreTrainedModel requires the PyTorch library but it was not found in your environment. Checkout the instructions on the
installation page: https://pytorch.org/get-started/locally/ and follow the ones that match your environment.
Please note that you may need to restart your runtime after installation.

Unexpected internal error when monkey patching `Trainer.train`: 
Trainer requires the PyTorch library but it was not found in your environment. Checkout the instructions on the
installation page: https://pytorch.org/get-started/locally/ and follow the ones that match your environment.
Please note that you may need to restart your runtime after installation.

Unexpected internal error when disabling torch.jit: No module named 'torch'


In [0]:
df_md = spark.table("edgar_md")
df_metadata = spark.table("edgar_metadata")

In [0]:
df_md.select('path', 'length').show(10, truncate=False)

+---------------------------------------------------------------------+-------+
|path                                                                 |length |
+---------------------------------------------------------------------+-------+
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-028573.md|1115973|
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001214659-24-006963.md|1108333|
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-032225.md|909727 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0000950170-24-038866.md|895801 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001437749-24-010430.md|841350 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001437749-24-012210.md|822294 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0000070858-24-000156.md|815434 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-036197.md|792620 |
|dbfs:/Volumes/llm_hackathon/default/edgar/mds/0000004904-24-000046.md|768371 |
|dbfs:/Volumes/llm_hackathon/default/edg

In [0]:
df_metadata.show(10)

+--------------------+------+-----------+-------+--------------------+--------------------+--------------+----------------+--------------------+
|        accession_no|  form|filing_date|    cik|                name|        display_name|       tickers|       exchanges|            industry|
+--------------------+------+-----------+-------+--------------------+--------------------+--------------+----------------+--------------------+
|0001493152-24-017204|  10-K| 2024-04-30|1855631|AERWINS Technolog...|AERWINS Technolog...| [AWIN, AWINW]|[Nasdaq, Nasdaq]|            Aircraft|
|0001762359-24-000023|  10-K| 2024-04-30|1762359|Acreage Holdings,...|Acreage Holdings,...|[ACRHF, ACRDF]|      [OTC, OTC]|Retail-Miscellane...|
|0001493152-24-017110|  10-K| 2024-04-30|1559998|Gaucho Group Hold...|Gaucho Group Hold...|        [VINO]|        [Nasdaq]|Land Subdividers ...|
|0001437749-24-013973|  10-K| 2024-04-30| 926423|MIND TECHNOLOGY, INC|MIND TECHNOLOGY, INC| [MIND, MINDP]|[Nasdaq, Nasdaq]|Search,

In [0]:
df_md = df_md.withColumn('accession_no', replace(element_at(split(df_md.path, '/'), -1), lit('.md'), lit('')))

In [0]:
df = df_md.join(df_metadata, 'accession_no', 'inner')

In [0]:
df.describe().show()

+-------+--------------------+--------------------+------------------+------+------------------+------------------+------------------+--------------------+
|summary|        accession_no|                path|            length|  form|               cik|              name|      display_name|            industry|
+-------+--------------------+--------------------+------------------+------+------------------+------------------+------------------+--------------------+
|  count|                1820|                1820|              1820|  1820|              1820|              1820|              1820|                1820|
|   mean|                NULL|                NULL|251662.64835164836|  NULL|1299939.8989010989|              NULL|              NULL|                NULL|
| stddev|                NULL|                NULL|174882.11469689873|  NULL| 545404.6719705774|              NULL|              NULL|                NULL|
|    min|0000002969-24-000026|dbfs:/Volumes/llm...|             

In [0]:
df = (df.withColumn('content_string', df.content.cast('string'))
        .withColumn('cik', df.cik.cast('string'))
        .withColumn('tickers', array_join(df.tickers, ', '))
        .withColumn('exchanges', element_at(df.exchanges, 1)))

In [0]:
max_chunk_size = 500
headers_to_split_on = [
    ("#", "Header 1"),
    ("##", "Header 2"),
    ("###", "Header 3"),
    ("####", "Header 4"),
]

tokenizer = OpenAIGPTTokenizer.from_pretrained("openai-gpt")
text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(tokenizer, chunk_size=max_chunk_size, chunk_overlap=50)
md_splitter = MarkdownHeaderTextSplitter(headers_to_split_on=headers_to_split_on, strip_headers=False)

# Split on headers, but merge small chunks together to avoid too small chunks.
def split_md(md, min_chunk_size=20, max_chunk_size=500):
    if not md:
        return []
    header_chunks = md_splitter.split_text(md)
    chunks = []
    previous_chunk = ""
    # Merge chunks together to add text before header and avoid too small docs.
    for c in header_chunks:
        content = c.metadata.get('Header 1', "") + "\n" + c.metadata.get('Header 2', "") + "\n" \
            + c.metadata.get('Header 3', "") + "\n" + c.metadata.get('Header 4', "") + "\n" \
            + c.page_content
        content = content.strip()
        if len(tokenizer.encode(previous_chunk + content)) <= max_chunk_size/2:
            previous_chunk += content + "\n"
        else:
            chunks.extend(text_splitter.split_text(previous_chunk.strip()))
            previous_chunk = content + "\n"
    if previous_chunk:
        chunks.extend(text_splitter.split_text(previous_chunk.strip()))
    # Discard too small chunks
    return [c for c in chunks if len(tokenizer.encode(c)) > min_chunk_size]

ftfy or spacy is not installed using BERT BasicTokenizer instead of SpaCy & ftfy.


In [0]:
md = df.limit(1).collect()[0]['content_string']

In [0]:
chunks = split_md(md)

Token indices sequence length is longer than the specified maximum sequence length for this model (283273 > 512). Running this sequence through the model will result in indexing errors


In [0]:
len(chunks)

632

In [0]:
chunks[0]

'**UNITED\nSTATES**  \n**SECURITIES\nAND EXCHANGE COMMISSION**  \n**WASHINGTON,\nDC 20549**  \n**FORM\n10-K**  \n**☒\nANNUAL REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934**  \n**For\nthe fiscal year ended December 31, 2023**  \n**or**  \n☐\n**TRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934**  \n**For\nthe transition period from\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0to**  \n**Commission\nFile Number 000-51274**  \n**FRONTIER\nFUNDS**  \n**FRONTIER\nDIVERSIFIED FUND;**  \n**FRONTIER\nLONG/SHORT COMMODITY FUND;**  \n**FRONTIER\nMASTERS FUND;**  \n**FRONTIER\nBALANCED FUND;**  \n**FRONTIER\nSELECT FUND;**  \n**FRONTIER\nGLOBAL FUND;**  \n**FRONTIER\nHERITAGE FUND**  \n**(Exact\nName of Registrant as specified in Its Charter)**  \n| **Delaware** |  | **36-6815533** |\n| --- | --- | --- |\n| **(State or Other Jurisdiction of  Incorporation or Organization)** |  | **(IRS Employer  Identification 

In [0]:
chunks[1]

'**Frontier\nLong/Short Commodity Fund Class 2, Class 3, Class 2a and Class 3a Units;**  \n**Frontier\nMasters Fund Class 2 and Class 3 Units;**  \n**Frontier\nBalanced Fund Class 1, Class 1AP, Class 2, Class 2a and Class 3a Units;**  \n**Frontier\nSelect Fund Class 1, Class 1AP, and Class 2 Units;**  \n**Frontier\nGlobal Fund Class 1 and Class 2 Units;**  \n**Frontier\nHeritage Fund Class 1, Class 1AP, and Class 2 Units**  \nIndicate\nby check mark if the registrant is a well-known seasoned issuer, as defined in Rule 405 of the Securities Act. Yes ☐ No ☒  \nIndicate\nby check mark if the registrant is not required to file reports pursuant to Section 13 or Section 15(d) of the Act. Yes ☐ No ☒  \nIndicate\nby check mark whether the registrant: (1) has filed all reports required to be filed by Section 13 or 15(d) of the Securities Exchange\nAct of 1934 during the preceding 12 months (or for such shorter period that the registrant was required to file such reports), and (2)\nhas been subj

In [0]:
chunks[2]

'| --- | --- | --- | --- | --- |\n| Non–Accelerated Filer | ☒ |  | Smaller Reporting Company | ☐ |\n|  |  |  | Emerging Growth Company | ☐ |  \nIf\nan emerging growth company, indicate by check mark if the registrant has elected not to use the extended transition period for complying\nwith any new or revised financial accounting standards provided pursuant to Section 13(a) of the Exchange Act. ☐  \nIndicate\nby check mark whether the registrant has filed a report on and attestation to its management’s assessment of the effectiveness\nof its internal control over financial reporting under\xa0Section 404(b) of the Sarbanes-Oxley Act\xa0(15 U.S.C. 7262(b)) by the\nregistered public accounting firm that prepared or issued its audit report. ☐  \nIf\nsecurities are registered pursuant to Section 12(b) of the Act, indicate by check mark whether the financial statements of the registrant\nincluded in the filing reflect the correction of an error to previously issued financial statements. ☐  \n

In [0]:
df.printSchema()

root
 |-- accession_no: string (nullable = true)
 |-- path: string (nullable = true)
 |-- modificationTime: timestamp (nullable = true)
 |-- length: long (nullable = true)
 |-- content: binary (nullable = true)
 |-- form: string (nullable = true)
 |-- filing_date: date (nullable = true)
 |-- cik: string (nullable = true)
 |-- name: string (nullable = true)
 |-- display_name: string (nullable = true)
 |-- tickers: string (nullable = true)
 |-- exchanges: string (nullable = true)
 |-- industry: string (nullable = true)
 |-- content_string: string (nullable = true)



In [0]:
@pandas_udf("array<string>")
def parse_and_split(docs: pd.Series) -> pd.Series:
    return docs.apply(split_md)

In [0]:
(df
    .withColumn('content', explode(parse_and_split('content_string')))
    .drop("modificationTime", "length", "content_string")
    .write.mode('overwrite').saveAsTable("edgar_form"))

In [0]:
df_edgar = spark.table("edgar_form")

In [0]:
display(df_edgar)

id accession_no path form filing_date cik name display_name tickers exchanges industry content 1 0001213900-24-028573 dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-028573.md 10-K 2024-04-01 1389122 Frontier Balanced Fund Frontier Balanced Fund null Commodity Contracts Brokers & Dealers **UNITED
STATES** 
**SECURITIES
AND EXCHANGE COMMISSION** 
**WASHINGTON,
DC 20549** 
**FORM
10-K** 
**☒
ANNUAL REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934** 
**For
the fiscal year ended December 31, 2023** 
**or** 
☐
**TRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934** 
**For
the transition period from                to** 
**Commission
File Number 000-51274** 
**FRONTIER
FUNDS** 
**FRONTIER
DIVERSIFIED FUND;** 
**FRONTIER
LONG/SHORT COMMODITY FUND;** 
**FRONTIER
MASTERS FUND;** 
**FRONTIER
BALANCED FUND;** 
**FRONTIER
SELECT FUND;** 
**FRONTIER
GLOBAL FUND;** 
**FRONTIER
HERITAGE FUND** 
**(Exact
Name of Registrant as specified in Its Charter)** 
| **Delaware** | | **36-6815533** |
| --- | --- | --- |
| **(State or Other Jurisdiction of Incorporation or Organization)** | | **(IRS Employer Identification No.)** | 
**c/o Frontier Fund Management, LLC
25568 Genesee Trail Road
Golden, Colorado 80401** 
**(Address of Principal Executive Offices)** 
**Registrant’s
Telephone Number, Including Area Code: (303) 454-5500** 
**Securities
registered pursuant to Section 12(b) of the Act:** 
| Title of each class | | Trading Symbol(s) | | Name of each exchange on which registered |
| --- | --- | --- | --- | --- |
| N/A | | N/A | | N/A | 
**Securities
registered pursuant to Section 12(g) of the Act:** 
**Title
of Each Class** 
**Frontier
Diversified Fund Class 2 and Class 3 Units;** 
**Frontier
Long/Short Commodity Fund Class 2, Class 3, Class 2a and Class 3a Units;** 
**Frontier
Masters Fund Class 2 and Class 3 Units;** 
**Frontier 7 0001213900-24-028573 dbfs:/Volumes/llm_hackathon/default/edgar/mds/0001213900-24-028573.md 10-K 2024-04-01 1389122 Frontier Balanced Fund Frontier Balanced Fund null Commodity Contracts Brokers & Dealers **Frontier
Long/Short Commodity Fund Class 2, Class 3, Class 2a and Class 3a Units;** 
**Frontier
Masters Fund Class 2 and Class 3 Units;** 
**Frontier
Balanced Fund Class 1, Class 1AP, Class 2, Class 2a and Class 3a Units;** 
**Frontier
Select Fund Class 1, Class 1AP, and Class 2 Units;** 
**Frontier
Global Fund Class 1 and Class 2 Units;** 
**Frontier
Heritage Fund Class 1, Class 1AP, and Class 2 Units** 
Indicate
by check mark if the registrant is a well-known seasoned issuer, as defined in Rule 405 of the Securities Act. Yes ☐ No ☒ 
Indicate
by check mark if the registrant is not required to file reports pursuant to Section 13 or Section 15(d) of the Act. Yes ☐ No ☒ 
Indicate
by check mark whether the registrant: (1) has filed all reports required to be filed by Section 13 or 15(d) of the Securities Exchange
Act of 1934 during the preceding 12 months (or for such shorter period that the registrant was required to file such reports), and (2)
has been subject to such filing requirements for the past 90 days. Yes ☒ No ☐ 
Indicate
by check mark whether the registrant has submitted electronically every Interactive Data File required to be submitted pursuant to Rule
405 of Regulation S-T (§232.405 of this chapter) during the preceding 12 months (or for such shorter period that the registrant
was required to submit such files). Yes ☒ No ☐ 
Indicate
by check mark whether the registrant is a large accelerated filer, an accelerated filer, a non-accelerated filer, a smaller reporting
company, or an emerging growth company. See the definitions of “large accelerated filer,” “accelerated filer,”
“smaller reporting company,” and “emerging growth company” in Rule 12b-2 of the Exchange Act. 
| Large Accelerated Filer | ☐ | | Accelerated Filer | ☐ |
| --- | --- | --- | --- | --- |
| Non–Accelerated Filer | ☒ | | Smaller Reporting Company | ☐ |
| | | | Emerg

In [0]:
%sql
SELECT COUNT(accession_no) FROM edgar_form

count(accession_no) 267344

In [0]:
%sql
SELECT COUNT(DISTINCT accession_no) FROM edgar_form

count(DISTINCT accession_no) 1820

In [0]:
%sql
SELECT industry, COUNT(DISTINCT accession_no)
FROM edgar_form
GROUP BY 1
ORDER BY 2 DESC

industry count(DISTINCT accession_no) Pharmaceutical Preparations 145 Blank Checks 115 Real Estate Investment Trusts 72 Services-Prepackaged Software 69 Surgical & Medical Instruments & Apparatus 48 Services-Business Services, NEC 42 Biological Products, (No Diagnostic Substances) 39 Crude Petroleum & Natural Gas 30 Services-Computer Programming, Data Processing, Etc. 29 State Commercial Banks 29 Services-Computer Processing & Data Preparation 28 Finance Services 26 Services-Computer Programming Services 23 Semiconductors & Related Devices 23 Real Estate 20 Miscellaneous Electrical Machinery, Equipment & Supplies 18 Asset-Backed Securities 16 Electric Services 16 Fire, Marine & Casualty Insurance 16 Services-Management Consulting Services 16 Retail-Eating Places 15 Communications Services, NEC 14 Investment Advice 14 Motor Vehicle Parts & Accessories 14 Medicinal Chemicals & Botanical Products 13 Retail-Miscellaneous Retail 13 Electromedical & Electrotherapeutic Apparatus 13 Orthopedic, Prosthetic & Surgical Appliances & Supplies 13 Metal Mining 13 Services-Advertising 12 Operative Builders 11 Services-Personal Services 11 Industrial Organic Chemicals 11 National Commercial Banks 11 Services-Computer Integrated Systems Design 10 Electric & Other Services Combined 10 Beverages 10 Food and Kindred Products 10 Heavy Construction Other Than Bldg Const - Contractors 10 10 Oil & Gas Field Services, NEC 10 Commodity Contracts Brokers & Dealers 9 Telephone Communications (No Radiotelephone) 9 Industrial Instruments For Measurement, Display, and Control 9 Perfumes, Cosmetics & Other Toilet Preparations 9 Insurance Agents, Brokers & Service 9 Retail-Auto Dealers & Gasoline Stations 8 Retail-Drug Stores and Proprietary Stores 8 Services-Equipment Rental & Leasing, NEC 8 Wholesale-Electronic Parts & Equipment, NEC 8 Services-Educational Services 8 Gold and Silver Ores 8 Motor Vehicles & Passenger Car Bodies 8 Life Insurance 8 In Vitro & In Vivo Diagnostic Substances 8 Industrial Inorganic Chemicals 7 Services-Misc Health & Allied Services, NEC 7 Services-Amusement & Recreation Services 7 Agricultural Production-Crops 7 Security Brokers, Dealers & Flotation Companies 7 Investors, NEC 7 Services-Health Services 7 Communications Equipment, NEC 7 Services-Miscellaneous Amusement & Recreation 7 Air Transportation, Scheduled 7 Services-Home Health Care Services 7 Oil & Gas Field Machinery & Equipment 7 Radio Broadcasting Stations 6 Retail-Family Clothing Stores 6 Special Industry Machinery, NEC 6 Laboratory Analytical Instruments 6 Retail-Catalog & Mail-Order Houses 6 Patent Owners & Lessors 6 Cable & Other Pay Television Services 6 Services-Medical Laboratories 6 Miscellaneous Manufacturing Industries 6 Services-Commercial Physical & Biological Research 6 Telephone & Telegraph Apparatus 6 Retail-Retail Stores, NEC 6 Miscellaneous Transportation Equipment 6 Petroleum Refining 6 Miscellaneous Chemical Products 6 Agricultural Chemicals 5 Personal Credit Institutions 5 Transportation Services 5 Electronic Components, NEC 5 Air-Cond & Warm Air Heatg Equip & Comm & Indl Refrig Equip 5 Hazardous Waste Management 5 Hotels & Motels 5 Plastic Materials, Synth Resins & Nonvulcan Elastomers 5 Oil Royalty Traders 5 Savings Institution, Federally Chartered 5 Railroads, Line-Haul Operating 5 Electronic & Other Electrical Equipment (No Computer Equip) 5 Real Estate Agents & Managers (For Others) 4 Search, Detection, Navigation, Guidance, Aeronautical Sys 4 Chemicals & Allied Products 4 Services-Specialty Outpatient Facilities, NEC 4 Radio & Tv Broadcasting & Communications Equipment 4 Services-Offices & Clinics of Doctors of Medicine 4 Services-Miscellaneous Equipment Rental & Leasing 4 Instruments For Meas & Testing of Electricity & Elec Signals 4 Natural Gas Transmission 4 Pumps & Pumping Equipment 4 Agricultural Services 4 Retail-Apparel & Accessory Stores 4 Aircraft 4 Plastics Products, NEC 4 Electric Lighting & Wiring Equipment 4 Hospital & Medical Servi

In [0]:
%sql
CREATE TABLE IF NOT EXISTS edgar_tech_form (
  id BIGINT GENERATED BY DEFAULT AS IDENTITY,
  accession_no STRING,
  path STRING,
  form STRING,
  filing_date DATE,
  cik STRING,
  name STRING,
  display_name STRING,
  tickers STRING,
  exchanges STRING,
  industry STRING,
  content STRING
) TBLPROPERTIES (delta.enableChangeDataFeed = true); 

In [0]:
(df_edgar
    .filter(df_edgar.industry.isin(["Services-Prepackaged Software", "Services-Computer Programming, Data Processing, Etc.",
                              "Services-Computer Processing & Data Preparation", "Services-Computer Programming Services"]))
    .write.mode('overwrite').saveAsTable("edgar_tech_form"))

In [0]:
(df_edgar
    .filter(df_edgar.industry.isin(["Services-Prepackaged Software", "Services-Computer Programming, Data Processing, Etc.",
                              "Services-Computer Processing & Data Preparation", "Services-Computer Programming Services"]))
    .select('name').distinct().sort('name').show(200))

+--------------------+
|                name|
+--------------------+
| ACI WORLDWIDE, INC.|
|AMJ Global Techno...|
|        APPFOLIO INC|
|         APPYEA, INC|
|         AUDDIA INC.|
|        AUDIOEYE INC|
|       Aceztech Corp|
|AdTheorent Holdin...|
|Airship AI Holdin...|
|       Alphabet Inc.|
|         Ankam, Inc.|
|AppTech Payments ...|
|Applied Digital C...|
|Appsoft Technolog...|
| Asset Entities Inc.|
|      Atlassian Corp|
|     BIOREGENX, INC.|
|      BLACKBERRY Ltd|
| BLACKBOXSTOCKS INC.|
|     Backblaze, Inc.|
|Banzai Internatio...|
|         Braze, Inc.|
|Bright Mountain M...|
|CADENCE DESIGN SY...|
|CCC Intelligent S...|
|           Crypto Co|
|Cyber App Solutio...|
|DESTINY MEDIA TEC...|
|      DIGIASIA CORP.|
|DUOS TECHNOLOGIES...|
|Data443 Risk Miti...|
|DecisionPoint Sys...|
|       E-Smart Corp.|
|E2open Parent Hol...|
|    EVERBRIDGE, INC.|
|Electronic Servit...|
|        Eva Live Inc|
|FACTSET RESEARCH ...|
|    Freeze Tag, Inc.|
|             GAN Ltd|
|   GOOD GA

In [0]:
%sql
SELECT COUNT(accession_no) FROM edgar_tech_form

count(accession_no) 20818

In [0]:
%sql
SELECT COUNT(DISTINCT accession_no) FROM edgar_tech_form

count(DISTINCT accession_no) 149

In [0]:
from databricks.vector_search.client import VectorSearchClient
vsc = VectorSearchClient()

vector_search_endpoint_name = "edgar_vs_endpoint"

vsc.create_endpoint(name=vector_search_endpoint_name, endpoint_type="STANDARD")

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().


{'name': 'edgar_vs_endpoint',
 'creator': 'zane.lim@worqhealth.com',
 'creation_timestamp': 1714641033206,
 'last_updated_timestamp': 1714641033206,
 'endpoint_type': 'STANDARD',
 'last_updated_user': 'zane.lim@worqhealth.com',
 'id': '17c2fd9a-aa93-4504-8952-4a4e81344044',
 'endpoint_status': {'state': 'PROVISIONING'},
 'num_indexes': 0}

In [0]:
from databricks.sdk import WorkspaceClient
import databricks.sdk.service.catalog as c

#The table we'd like to index
source_table_fullname = "llm_hackathon.default.edgar_tech_form"
# Where we want to store our index
vs_index_fullname = "llm_hackathon.default.edgar_form_vs_index"

vsc.create_delta_sync_index(
    endpoint_name=vector_search_endpoint_name,
    index_name=vs_index_fullname,
    source_table_name=source_table_fullname,
    pipeline_type="TRIGGERED",
    primary_key="id",
    embedding_source_column='content', #The column containing our text
    embedding_model_endpoint_name='databricks-bge-large-en' #The embedding endpoint used to create the embeddings
)

In [0]:
from langchain_community.vectorstores import DatabricksVectorSearch
from langchain_community.embeddings import DatabricksEmbeddings

In [0]:
embedding_model = DatabricksEmbeddings(endpoint="databricks-bge-large-en")

vs_index = vsc.get_index(
    endpoint_name=vector_search_endpoint_name,
    index_name=vs_index_fullname
)

# Create the retriever
vectorstore = DatabricksVectorSearch(
    vs_index, text_column="content", embedding=embedding_model,
    columns=['name', 'tickers', 'form']
)

retriever = vectorstore.as_retriever(search_kwargs={"k" : 5})

embedding model is not used in delta-sync index with Databricks-managed embeddings.


In [0]:
similar_documents = retriever.get_relevant_documents("What was alphabet's revenue?")

/local_disk0/.ephemeral_nfs/envs/pythonEnv-ebb9aff4-1035-4d91-b80a-0c9372d59f4f/lib/python3.11/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The method `BaseRetriever.get_relevant_documents` was deprecated in langchain-core 0.1.46 and will be removed in 0.3.0. Use invoke instead.
  warn_deprecated(


In [0]:
similar_documents

[Document(page_content='---  \n|  |  |  |  |  |  |\n| --- | --- | --- | --- | --- | --- |\n|  | | | Alphabet Inc. | | |  \nNote 2. Revenues Disaggregated RevenuesThe following table presents revenues disaggregated by type (in millions):  \n|  |  |  |  |  |  |  |  |  |  |  |  |  | | |  | | |  | | |  | | |\n| --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- | --- |\n|  | | | Three Months Ended | | | | | | | | |  | | |  | | |\n|  | | | March 31, | | | | | | | | |  | | |  | | |\n|  | | | 2023 | | |  | | | 2024 | | |  | | |  | | |  | | |  | | |\n| Google Search & other | | | $ | 40,359 |  |  | | | $ | 46,156 |  |  | | |  | | |  | | |  | | |\n| YouTube ads | | | 6,693 | |  |  | | | 8,090 | |  |  | | |  | | |  | | |  | | |\n| Google Network | | | 7,496 | |  |  | | | 7,413 | |  |  | | |  | | |  | | |  | | |\n| Google advertising | | | 54,548 | |  |  | | | 61,659 | |  |  | | |  | | |  | | |  | | |\n| Google s